Based on: 
https://github.com/ProjectPythia/interactive-sentinel-2-cookbook/blob/main/notebooks/data-intake-ms-planetary-computer.ipynb

Resources and references

    Orignal authored by Pritam Das (@pritamd47), June 2023 during Project Pythia cookoff 2023.
    This notebook takes a lot of inspiration from the Landsat ML Cookbook by Demetris Roumis.
    This notebook uses concepts and code illustrated in the Reading Data from the STAC API.


In [1]:
import os
import pandas as pd
import numpy as np
import xarray as xr
import pystac_client
import planetary_computer
import panel as pn
import panel.widgets as pnw
import hvplot.xarray
import holoviews as hv
import geoviews as gv
from pystac.extensions.eo import EOExtension as eo
import datetime
from cartopy import crs
from dask.distributed import Client, LocalCluster
import odc.stac

xr.set_options(keep_attrs=True)
hv.extension('bokeh')
gv.extension('bokeh')

In [20]:
nworkers = os.cpu_count()
print('nworkers = ', nworkers)
cluster = LocalCluster(n_workers=os.cpu_count())
client = Client(cluster)
client

nworkers =  24


C:\Users\csherwood\Anaconda3\envs\satellites\Lib\site-packages\distributed\node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 53005 instead
  warnings.warn(
C:\Users\csherwood\Anaconda3\envs\satellites\Lib\contextlib.py:144: UserWarning: Creating scratch directories is taking a surprisingly long time. (1.83s) This is often due to running workers on a network file system. Consider specifying a local-directory to point workers to write scratch data to a local disk.
  next(self.gen)


<Client: 'tcp://127.0.0.1:53006' processes=24 threads=24, memory=63.89 GiB>

In [6]:
stac_root = 'https://planetarycomputer.microsoft.com/api/stac/v1'
catalog = pystac_client.Client.open(
    stac_root,
    modifier=planetary_computer.sign_inplace
)
print(f"{catalog.title} - {catalog.description}")


sentinel2_collections = [collection for collection in catalog.get_collections() if "sentinel-2" in collection.id]
sentinel2_collections

Microsoft Planetary Computer STAC API - Searchable spatiotemporal metadata describing Earth science datasets hosted by the Microsoft Planetary Computer


[<CollectionClient id=sentinel-2-l2a>]

In [10]:
bbox = [-76.310349,34.851566,-76.024017,35.094631] # N. Core Banks  from http://bboxfinder.com/
#bbox = [-105.283263,39.972809,-105.266569,39.987640] # NCAR, boulder, CO. bbox from http://bboxfinder.com/
date_range = "2022-01-01/2022-12-31"
collection = "sentinel-2-l2a"                        # full id of collection
cloud_thresh = 30

In [11]:
search = catalog.search(
    collections = sentinel2_collections,
    bbox = bbox,
    datetime = date_range,
    query={"eo:cloud_cover": {"lt": cloud_thresh}}
)
items = search.item_collection()
print(f"Found {len(items)} items in the {collection}")

Found 111 items in the sentinel-2-l2a


In [12]:
first_item = items.items[0]
all_bands = list(first_item.assets.keys())
print("Assets available:")
print(*all_bands, sep=', ')

Assets available:
AOT, B01, B02, B03, B04, B05, B06, B07, B08, B09, B11, B12, B8A, SCL, WVP, visual, preview, safe-manifest, granule-metadata, inspire-metadata, product-metadata, datastrip-metadata, tilejson, rendered_preview


In [19]:
first_item

<Item id=S2B_MSIL2A_20221228T154649_R011_T18SVD_20221230T004203>

In [13]:
bands_of_interest = [b for b in all_bands if b.startswith('B')]

da = odc.stac.stac_load(
    items,
    bands=bands_of_interest,
    bbox=bbox,
    chunks={},  # <-- use Dask
).to_array(dim='band')
da

<xarray.DataArray (band: 12, time: 63, y: 2727, x: 2647)>
dask.array<stack, shape=(12, 63, 2727, 2647), dtype=float32, chunksize=(1, 1, 2727, 2647), chunktype=numpy.ndarray>
Coordinates:
  * y            (y) float64 3.884e+06 3.884e+06 ... 3.857e+06 3.857e+06
  * x            (x) float64 3.802e+05 3.802e+05 ... 4.067e+05 4.067e+05
    spatial_ref  int32 32618
  * time         (time) datetime64[ns] 2022-01-02T15:46:39.024000 ... 2022-12...
  * band         (band) object 'B01' 'B02' 'B03' 'B04' ... 'B11' 'B12' 'B8A'

In [14]:
# from https://planetarycomputer.microsoft.com/dataset/sentinel-2-l2a#Baseline-Change
def harmonize_to_old(data):  
    """
    Harmonize new Sentinel-2 data to the old baseline.

    Parameters
    ----------
    data: xarray.DataArray
        A DataArray with four dimensions: time, band, y, x

    Returns
    -------
    harmonized: xarray.DataArray
        A DataArray with all values harmonized to the old
        processing baseline.
    """
    cutoff = datetime.datetime(2022, 1, 25)
    offset = 1000
    bands = ["B01","B02","B03","B04","B05","B06","B07","B08","B8A","B09","B10","B11","B12"]

    old = data.sel(time=slice(cutoff))

    to_process = list(set(bands) & set(data.band.data.tolist()))
    new = data.sel(time=slice(cutoff, None)).drop_sel(band=to_process)

    new_harmonized = data.sel(time=slice(cutoff, None), band=to_process).clip(offset)
    new_harmonized -= offset

    new = xr.concat([new, new_harmonized], "band").sel(band=data.band.data.tolist())
    return xr.concat([old, new], dim="time")

da = harmonize_to_old(da)
da

<xarray.DataArray (band: 12, time: 63, y: 2727, x: 2647)>
dask.array<concatenate, shape=(12, 63, 2727, 2647), dtype=float32, chunksize=(1, 1, 2727, 2647), chunktype=numpy.ndarray>
Coordinates:
  * y            (y) float64 3.884e+06 3.884e+06 ... 3.857e+06 3.857e+06
  * x            (x) float64 3.802e+05 3.802e+05 ... 4.067e+05 4.067e+05
    spatial_ref  int32 32618
  * time         (time) datetime64[ns] 2022-01-02T15:46:39.024000 ... 2022-12...
  * band         (band) object 'B01' 'B02' 'B03' 'B04' ... 'B11' 'B12' 'B8A'

In [15]:
da = da / 1e4   # Scale data values from 0:10000 to 0:1.0
da = da / da.max(dim='band')  # additionally scale from 0-max -> 0-1 for visual quality
da = da.compute()

2023-08-09 14:34:39,268 - distributed.nanny.memory - WARNING - Worker tcp://127.0.0.1:52765 (pid=6636) exceeded 95% memory budget. Restarting...
2023-08-09 14:34:41,718 - distributed.nanny - WARNING - Restarting worker
2023-08-09 14:34:54,183 - distributed.scheduler - ERROR - Couldn't gather keys {"('truediv-078f7d3faed76da13ebc1d6d4f83a889', 11, 58, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 11, 1, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 3, 2, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 7, 17, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 3, 20, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 0, 30, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 0, 17, 0, 0)": ['tcp://127.0.0.1:52765'], "('truediv-078f7d3faed76da13ebc1d6d4f83a889', 9, 56, 0, 0)": ['tcp://127.0.0.1:52765'

2023-08-09 14:34:54,253 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 11, 58, 0, 0)
NoneType: None
2023-08-09 14:34:54,253 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 11, 1, 0, 0)
NoneType: None
2023-08-09 14:34:54,254 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 3, 2, 0, 0)
NoneType: None
2023-08-09 14:34:54,255 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 7, 17, 0, 0)
NoneType: None
2023-08-09 14:34:54,256 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889'

2023-08-09 14:34:54,281 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 8, 1, 0, 0)
NoneType: None
2023-08-09 14:34:54,283 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 8, 30, 0, 0)
NoneType: None
2023-08-09 14:34:54,283 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 9, 13, 0, 0)
NoneType: None
2023-08-09 14:34:54,284 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 0, 13, 0, 0)
NoneType: None
2023-08-09 14:34:54,284 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889',

2023-08-09 14:34:54,307 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 9, 7, 0, 0)
NoneType: None
2023-08-09 14:34:54,307 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 6, 23, 0, 0)
NoneType: None
2023-08-09 14:34:54,308 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 4, 56, 0, 0)
NoneType: None
2023-08-09 14:34:54,308 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889', 1, 14, 0, 0)
NoneType: None
2023-08-09 14:34:54,310 - distributed.scheduler - ERROR - Shut down workers that don't have promised key: ['tcp://127.0.0.1:52765'], ('truediv-078f7d3faed76da13ebc1d6d4f83a889',

In [16]:
def plot_band(band, cmap):
    return da.sel(band=band).isel(time=0).hvplot(
        x='x', y='y', data_aspect=1, 
        cmap=cmap, geo=True, tiles='ESRI', 
        crs=crs.epsg(items[0].properties['proj:epsg']), rasterize=True,
        title=f"band: {band}, cmap: {cmap}",
        clabel='surface reflectance [0.0-1.0]'
    ).opts(
        frame_width=300,
        xlabel='longitude',
        ylabel='latitude',
        
    )

(plot_band('B04', 'Blues') + plot_band('B03', 'Greens') + plot_band('B02', 'Reds')).cols(2)

:Layout
   .DynamicMap.I   :DynamicMap   []
      :Overlay
         .Tiles.I :Tiles   [x,y]
         .Image.I :Image   [x,y]   (value)
   .DynamicMap.II  :DynamicMap   []
      :Overlay
         .Tiles.I :Tiles   [x,y]
         .Image.I :Image   [x,y]   (value)
   .DynamicMap.III :DynamicMap   []
      :Overlay
         .Tiles.I :Tiles   [x,y]
         .Image.I :Image   [x,y]   (value)

In [17]:
def rgb_during(time):
    season_names = {
        1: 'Winter',
        2: 'Spring',
        3: 'Summer',
        4: 'Fall'
    }
    da_rgb = da.sel(band=['B04', 'B03', 'B02'])
    start_date = pd.to_datetime(da_rgb['time'].min().data).to_pydatetime()
    end_date = pd.to_datetime(da_rgb['time'].max().data).to_pydatetime()
    closest_date = pd.to_datetime(da_rgb.sel(time=time, method='nearest').time.data).to_pydatetime()
    dt_slider = pnw.DateSlider(name='Date', start=start_date, end=end_date, value=closest_date)
    
    def get_obs_on(t):
        season_key = [month%12 // 3 + 1 for month in range(1, 13)][t.month-1]
        season = season_names[season_key]
        return da.sel(band=['B04', 'B03', 'B02']).sel(time=t, method='nearest').transpose('y', 'x', 'band').hvplot.rgb(
            x='x', y='y', bands='band', 
            geo=True, tiles='ESRI', crs=crs.epsg(items[0].properties['proj:epsg']), 
            rasterize=True, title=f"{season}: {t.strftime('%Y-%m-%d')}"
        ).opts(
            frame_width=300,
            xlabel='longitude',
            ylabel='latitude',
        )
        
    
    return pn.panel(pn.Column(
                pn.bind(get_obs_on, t=dt_slider), 
                pn.Row(
                    pn.Spacer(width=60),
                    dt_slider,
                )
            ))

In [18]:


rgb_during('2022-02-01')



Column
    [0] ParamFunction(function, _pane=HoloViews, defer_load=False)
    [1] Row
        [0] Spacer(width=60)
        [1] DateSlider(end=datetime.datetime(2022, ..., name='Date', start=datetime.datetime(2022, ..., value=datetime.datetime(2022, ...)